# Recipe Ratings in Comparison to Cooking Time

**Name(s)**: Tea Hajratwala, Devdeep Rajpal

**Website Link**: https://recipe-analysis.github.io/recipe-analysis/

In [8]:
import pandas as pd
import numpy as np

import plotly.express as px
pd.options.plotting.backend = 'plotly'

from lec_utils import * # Feel free to uncomment and use this. It'll make your plotly graphs look like ours in lecture!

# Load the data
recipes = pd.read_csv('data/raw_recipes.csv')
recipe_interactions = pd.read_csv('data/raw_interactions.csv')

## Step 1: Introduction

The data:

In [9]:
recipe_interactions

user_id  recipe_id        date  rating  \
0          1293707      40893  2011-12-21       5   
1           126440      85009  2010-02-27       5   
2            57222      85009  2011-10-01       5   
...            ...        ...         ...     ...   
731924      157126      78003  2008-06-23       5   
731925       53932      78003  2009-01-11       4   
731926  2001868099      78003  2017-12-18       5   

                                                   review  
0       So simple, so delicious! Great for chilly fall...  
1       I made the Mexican topping and took it to bunk...  
2       Made the cheddar bacon topping, adding a sprin...  
...                                                   ...  
731924  WOW!  Sometimes I don't take the time to rate ...  
731925  Very good!  I used regular port as well.  The ...  
731926  I am so glad I googled and found this here. Th...  

[731927 rows x 5 columns]

In [10]:
recipe_interactions.columns

Index(['user_id', 'recipe_id', 'date', 'rating', 'review'], dtype='object')

In [11]:
recipes

name      id  minutes  \
0              1 brownies in the world    best ever  333281       40   
1                1 in canada chocolate chip cookies  453467       45   
2                            412 broccoli casserole  306168       40   
...                                             ...     ...      ...   
83779                     zydeco ya ya deviled eggs  308080       40   
83780        cookies by design   cookies on a stick  298512       29   
83781  cookies by design   sugar shortbread cookies  298509       20   

       contributor_id  ...                                              steps  \
0              985201  ...  ['heat the oven to 350f and arrange the rack i...   
1             1848091  ...  ['pre-heat oven the 350 degrees f', 'in a mixi...   
2               50969  ...  ['preheat oven to 350 degrees', 'spray a 2 qua...   
...               ...  ...                                                ...   
83779           37779  ...  ['in a bowl , combine the mashed yolks and may...   
83780          506822  ...  ['place melted butter in a large mixing bowl a...   
83781          506822  ...  ['whip sugar and shortening in a large bowl , ...   

                                             description  \
0      these are the most; chocolatey, moist, rich, d...   
1      this is the recipe that we use at my school ca...   
2      since there are already 411 recipes for brocco...   
...                                                  ...   
83779                          deviled eggs, cajun-style   
83780  i've heard of the 'cookies by design' company,...   
83781  i've heard of the 'cookies by design' company,...   

                                             ingredients  n_ingredients  
0      ['bittersweet chocolate', 'unsalted butter', '...              9  
1      ['white sugar', 'brown sugar', 'salt', 'margar...             11  
2      ['frozen broccoli cuts', 'cream of chicken sou...              9  
...                                                  ...            ...  
83779  ['hard-cooked eggs', 'mayonnaise', 'dijon must...              8  
83780  ['butter', 'eagle brand condensed milk', 'ligh...             10  
83781  ['granulated sugar', 'shortening', 'eggs', 'fl...              7  

[83782 rows x 12 columns]

In [12]:
recipes.columns

Index(['name', 'id', 'minutes', 'contributor_id', 'submitted', 'tags',
       'nutrition', 'n_steps', 'steps', 'description', 'ingredients',
       'n_ingredients'],
      dtype='object')

The `nutrition` column looks interesting-- all the nutritional values are listed here. We will have to process the data a little extra, but it would be cool to do an analysis on the nutritional values in each recipe (i.e. predict the `calories` or `protein`). This could have cool implications for looking for "healthy" recipes when trying to hit a certain diatary need.
Another idea would be to take a look at the `tags` and compare them to the nutritional values of each tag and observe the general trends.

Here's the question we ended up investigating: Which tags have the highest protein to carb ratio?

## Step 2: Data Cleaning and Exploratory Data Analysis

In [13]:
# Left merge the recipes and interactions datasets together.
recipe_interactions['recipe_id'] = recipe_interactions['recipe_id'].astype(int)
recipes_interactions_merged = recipes.merge(recipe_interactions, left_on='id', right_on='recipe_id', how='left')
recipes_interactions_merged.head()

name      id  minutes  contributor_id  ...  \
0  1 brownies in the world    best ever  333281       40          985201  ...   
1    1 in canada chocolate chip cookies  453467       45         1848091  ...   
2                412 broccoli casserole  306168       40           50969  ...   
3                412 broccoli casserole  306168       40           50969  ...   
4                412 broccoli casserole  306168       40           50969  ...   

  recipe_id        date rating  \
0  333281.0  2008-11-19    4.0   
1  453467.0  2012-01-26    5.0   
2  306168.0  2008-12-31    5.0   
3  306168.0  2009-04-13    5.0   
4  306168.0  2013-08-02    5.0   

                                              review  
0  These were pretty good, but took forever to ba...  
1  Originally I was gonna cut the recipe in half ...  
2  This was one of the best broccoli casseroles t...  
3  I made this for my son's first birthday party ...  
4  Loved this.  Be sure to completely thaw the br...  

[5 rows x 17 columns]

In [14]:
# In the merged dataset, fill all ratings of 0 with np.nan. (Think about why this is a reasonable step, and include your justification in your website.)
recipes_interactions_merged['rating'] = recipes_interactions_merged['rating'].replace(0, np.nan)

The justification for filling all ratings having value 0 with `np.nan` is that when we compute the mean, we want to ignore the zero value (as it is not possible without a recipe recieving literally 0 ratings). Pandas will automatically ignore any rows with `np.nan` when computing the mean. 

In [15]:
# Find the average rating per recipe, as a Series.

#attempt at filter out recipes with less than 5 ratings
#avg_ratings = recipe_interactions.groupby('recipe_id').filter(lambda x: len(x) >= 5)

avg_ratings = recipes_interactions_merged.groupby('recipe_id')['rating'].mean().reset_index()
avg_ratings.columns = ['recipe_id', 'avg_rating']
avg_ratings['recipe_id'] = avg_ratings['recipe_id'].astype(int)
avg_ratings

recipe_id  avg_rating
0         275022         3.0
1         275024         3.0
2         275026         3.0
...          ...         ...
83778     537543         NaN
83779     537671         NaN
83780     537716         5.0

[83781 rows x 2 columns]

In [16]:
recipe_interactions.columns

Index(['user_id', 'recipe_id', 'date', 'rating', 'review'], dtype='object')

In [17]:
recipes.columns
recipes.iloc[0].transpose().to_frame()[5:10]

0
tags         ['60-minutes-or-less', 'time-to-make', 'course...
nutrition             [138.4, 10.0, 50.0, 3.0, 3.0, 19.0, 6.0]
n_steps                                                     10
steps        ['heat the oven to 350f and arrange the rack i...
description  these are the most; chocolatey, moist, rich, d...

In [18]:
recipes_avg_merged = recipes_interactions_merged.merge(avg_ratings, on='recipe_id', how='left')
recipes_f = recipes_avg_merged.set_index('recipe_id')
recipes_f['avg_rating'] = avg_ratings.set_index('recipe_id')['avg_rating']
recipes_full = recipes_f.groupby('recipe_id').agg({
    'name': 'first',
    'id': 'first',
    'minutes': 'first',
    'contributor_id': 'first',
    'submitted': 'first',
    'tags': 'first',
    'nutrition': 'first',
    'n_steps': 'first',
    'steps': 'first',
    'description': 'first',
    'ingredients': 'first',
    'n_ingredients': 'first',
    'user_id': lambda x: list(x),
    'date': 'first',
    'avg_rating': 'first',
    'review': lambda x: list(x)
}).reset_index()
recipes_full

# Convert the 'nutrition' column from string to list
recipes_full['nutrition'] = recipes_full['nutrition'].apply(eval)

# Create individual columns for each nutritional value
nutrition_columns = ['calories', 'total_fat', 'sugar', 'sodium', 'protein', 'saturated_fat', 'carbohydrates']
nutrition_df = pd.DataFrame(recipes_full['nutrition'].tolist(), columns=nutrition_columns, index=recipes_full.index)

# Concatenate the new columns with the original dataframe
recipes_full = pd.concat([recipes_full, nutrition_df], axis=1)

# Drop the original 'nutrition' column
recipes_full = recipes_full.drop(columns=['nutrition'])
df = recipes_full.copy()
recipes_full.head()

recipe_id                                   name      id  minutes  ...  \
0   275022.0     impossible macaroni and cheese pie  275022       50  ...   
1   275024.0                 impossible rhubarb pie  275024       55  ...   
2   275026.0                 impossible seafood pie  275026       45  ...   
3   275030.0  paula deen s caramel apple cheesecake  275030       45  ...   
4   275032.0                   midori poached pears  275032       25  ...   

   sodium protein saturated_fat  carbohydrates  
0    24.0    41.0          62.0            8.0  
1    13.0    13.0          30.0           20.0  
2    27.0    37.0          51.0            5.0  
3    19.0    14.0          67.0           21.0  
4     0.0     1.0           0.0           33.0  

[5 rows x 23 columns]

### Univariate Data Analysis

In [19]:
# Plot the minutes column as a boxplot. (You can use the default bins, or specify your own.)

fig = px.box(recipes_full, y='minutes')
fig.update_layout(
    title='Preparation Time',
    yaxis_title='Preparation Time (minutes)'
)
fig.show()
fig.write_html('univariate_analysis_prep_time.html', include_plotlyjs='cdn')

You can see that the boxplot has some significant outliers-- There is one recipe that takes 1.05 *million* minutes! We will need to remove these outliers to do most of the data analysis.

Let's take a look at the top outliers:

In [20]:
recipes_full.sort_values('minutes', ascending=False).head(10)

recipe_id                       name      id  minutes  ...  sodium  \
65941   447963.0  how to preserve a husband  447963  1051200  ...     1.0   
7738    291571.0     homemade fruit liquers  291571   288000  ...     0.0   
59812   425681.0           homemade vanilla  425681   259205  ...     0.0   
...          ...                        ...     ...      ...  ...     ...   
63155   437385.0     sauerkraut in a bottle  437385    60510  ...    48.0   
63189   437520.0    simple hard apple cider  437520    53290  ...     0.0   
15630   309383.0             pickled olives  309383    50410  ...   254.0   

      protein saturated_fat  carbohydrates  
65941     7.0         115.0            5.0  
7738      0.0           0.0           27.0  
59812     0.0           0.0            0.0  
...       ...           ...            ...  
63155     1.0           0.0            1.0  
63189     0.0           0.0           31.0  
15630     3.0          22.0            1.0  

[10 rows x 23 columns]

It appears that these are mostly pickling/marinating/fermenting recipes, which take a long time. Thankfully, the `tags` column contains a tag that labels recipes that take `1-day-or-more`-- Let's filter those out.

In [21]:
univar_data = recipes_full[recipes_full['tags'].str.contains('1-day-or-more') == False]
univar_data = univar_data[univar_data['minutes'] < 1440]
univar_data

recipe_id                                        name      id  minutes  \
0       275022.0          impossible macaroni and cheese pie  275022       50   
1       275024.0                      impossible rhubarb pie  275024       55   
2       275026.0                      impossible seafood pie  275026       45   
...          ...                                         ...     ...      ...   
83778   537543.0                      moist gingerbread cake  537543       55   
83779   537671.0  nutcracker peppermint red velvet cake pops  537671      135   
83780   537716.0           mini buffalo chicken cheesesteaks  537716       40   

       ...  sodium protein saturated_fat  carbohydrates  
0      ...    24.0    41.0          62.0            8.0  
1      ...    13.0    13.0          30.0           20.0  
2      ...    27.0    37.0          51.0            5.0  
...    ...     ...     ...           ...            ...  
83778  ...     8.0    40.0         203.0           80.0  
83779  ...    10.0     6.0           8.0           10.0  
83780  ...    49.0    28.0          64.0           12.0  

[83151 rows x 23 columns]

In [22]:
fig = px.box(univar_data, y='minutes')
fig.update_layout(
    title='Preparation Time (Excluding 1-day-or-more)',
    yaxis_title='Preparation Time (minutes)'
)
fig.show()


In [23]:
import ipywidgets as widgets
from ipywidgets import interact
from IPython.display import clear_output

# Display the avg_rating column as a histogram, allowing the user to specify the number of bins.
def update_histogram(bins):
    clear_output(wait=False)
    fig = px.histogram(avg_ratings, x='avg_rating', nbins=bins)
    fig.update_layout(
        title='Distribution of Average Ratings (slide to change number of bins)',
        xaxis_title='Average Rating (/5)',
        yaxis_title='Count'
    )
    fig.show()

interact(update_histogram, bins=widgets.IntSlider(min=1, max=50, step=1, value=5))
fig.write_html('univariate_analysis_rating_dist.html', include_plotlyjs='cdn')

interactive(children=(IntSlider(value=5, description='bins', max=50, min=1), Output()), _dom_classes=('widget-…

It appears that the vast majority of average ratings are positive. Even when increasing the histogram bin size (and increasing granularity), the rightmost bin consistently has the highest number of recipes.

### Bivariate Data Analysis

In [24]:
bivar_data = recipes_full[['avg_rating', 'minutes', 'name', 'tags']]
bivar_data = bivar_data.sort_values('minutes', ascending=False)

# print the tags of the first 5 recipes without truncating
# '1-day-or-more'
bivar_data.head()['tags']

65941    ['time-to-make', 'course', 'preparation', 'for...
7738     ['time-to-make', 'course', 'main-ingredient', ...
59812    ['time-to-make', 'preparation', '5-ingredients...
70811    ['time-to-make', 'preparation', 'occasion', 'f...
62769    ['time-to-make', 'course', 'main-ingredient', ...
Name: tags, dtype: object

In [25]:
# drop all rows where the tags column contains '1-day-or-more'
bivar_data = bivar_data[bivar_data['tags'].str.contains('1-day-or-more') == False]
bivar_cleaned = bivar_data.dropna()
bivar_cleaned = bivar_cleaned[bivar_cleaned['avg_rating'] > 0]
bivar_cleaned = bivar_cleaned[bivar_cleaned['minutes'] > 0]

# drop rows where minutes is greater than 1440 (1 day)
bivar_cleaned = bivar_cleaned[bivar_cleaned['minutes'] <= 1440]

fig = px.scatter(bivar_cleaned, x='avg_rating', y='minutes')
fig.update_layout(
                  title='Average User Rating vs. Preparation Time ',
                  xaxis_title='Average User Rating (/5)',
                  yaxis_title='Preparation Time (minutes)',
                  )
fig.show()

In [26]:
# What types of recipes tend to be healthier (i.e. more protein, fewer carbs)?
# Create a new column 'protein_to_carb_ratio' that contains the ratio of protein to carbohydrates.
recipes_full = df.copy()
# drop rows where the protein or carbs equals 0 
recipes_full = recipes_full[recipes_full['protein'] > 0]
recipes_full = recipes_full[recipes_full['carbohydrates'] > 0]

recipes_full['protein_to_carb_ratio'] = recipes_full['protein'] // recipes_full['carbohydrates']

# for each row, create a new row with one of the tags in the tags list, along with the protein to carb ratio
recipes_bivar_2 = recipes_full.copy()
recipes_bivar_2['protein_to_carb_ratio'] = recipes_bivar_2['protein'] / recipes_bivar_2['carbohydrates']

# convert the tags column to a list
recipes_bivar_2['tags'] = recipes_bivar_2['tags'].apply(eval) 

# explode the tags column (one tag per row)
recipes_bivar_2 = recipes_bivar_2.explode('tags')

# find the top 25 most common tags
top_tags = recipes_bivar_2['tags'].value_counts().head(25).index

# remove all rows where the tag is not in the top 25
recipes_bivar_2 = recipes_bivar_2[recipes_bivar_2['tags'].isin(top_tags)]
recipes_bivar_2 = recipes_bivar_2.set_index('recipe_id')
recipes_bivar_2.sort_values('protein_to_carb_ratio', inplace=True)

# find the mean protein to carb ratio for each tag
recipes_bivar_3 = recipes_bivar_2.groupby('tags').agg({'protein_to_carb_ratio': 'mean'}).reset_index()
# Order the bars in the bar chart in descending order of protein to carb ratio
recipes_bivar_3 = recipes_bivar_3.sort_values('protein_to_carb_ratio', ascending=False)
# plot each tag and its average protein to carb ratio in bar chart
fig = px.bar(
            recipes_bivar_3, 
            x='tags',
            y='protein_to_carb_ratio'
            )
fig.update_layout(
    title='Average Protein to Carb Ratio for the 25 Most Common Tags',
    xaxis_title='Tag',
    yaxis_title='Average Protein to Carb Ratio'
)
fig.show()


You can see (not surprisingly) that the recipes with the highest average protein to carb ratio are `low-carb` and `meat` recipes. Surprisingly, recipes labelled as `healthy` have some of the lowest protein to carb ratios in the top 25 most common tags.

### Interesting Aggregates
Another way of visuallizing the data above in a less condensed way is with a grouped table:

In [27]:
recipes_full = df.copy()

# for each row, create a new row with one of the tags in the tags list, along with the protein to carb ratio
recipes_bivar_2 = recipes_full.copy()
recipes_bivar_2['protein_to_carb_ratio'] = recipes_bivar_2['protein'] / recipes_bivar_2['carbohydrates']

# convert the tags column to a list
recipes_bivar_2['tags'] = recipes_bivar_2['tags'].apply(eval) 

# explode the tags column (one tag per row)
recipes_bivar_2 = recipes_bivar_2.explode('tags')

# find the top 25 most common tags
top_tags = recipes_bivar_2['tags'].value_counts().head(25).index

# remove all rows where the tag is not in the top 25
recipes_bivar_2 = recipes_bivar_2[recipes_bivar_2['tags'].isin(top_tags)]
recipes_bivar_2 = recipes_bivar_2.set_index('recipe_id')

recipes_grouped = recipes_bivar_2.groupby('tags')[['calories', 'total_fat', 'sugar', 'sodium', 'protein', 'saturated_fat', 'carbohydrates']].mean()
recipes_grouped


calories  total_fat  sugar  sodium  protein  \
tags                                                              
15-minutes-or-less    313.67      24.27  67.95   26.50    17.33   
3-steps-or-less       358.43      26.50  63.86   28.43    25.83   
30-minutes-or-less    375.63      28.58  48.96   23.48    31.69   
...                      ...        ...    ...     ...      ...   
taste-mood            453.66      35.18  67.23   28.54    35.84   
time-to-make          427.36      32.48  69.10   28.40    32.08   
vegetables            336.17      25.98  34.89   25.70    26.13   

                    saturated_fat  carbohydrates  
tags                                              
15-minutes-or-less          28.18          10.38  
3-steps-or-less             31.03          11.78  
30-minutes-or-less          34.24          11.62  
...                           ...            ...  
taste-mood                  44.86          14.10  
time-to-make                40.09          13.84  
vegetables                  29.45          10.76  

[25 rows x 7 columns]

Here, we have left the data in its raw form (ie. not in ratos).

### Imputation *DEV CAN YOU FINISH THIS PART*
We have imputed the data to *remove* missing data. We did this because ultimately the imputed dataset is still large enough to be representative of the raw dataset, and ultimatlely it doesn't affect the appearance or shape of the data. See below:

In [28]:
# show the imputation doesnt change the data
# Create a new column 'protein_to_carb_ratio' that contains the ratio of protein to carbohydrates.
recipes_full = df.copy()

# for each row, create a new row with one of the tags in the tags list, along with the protein to carb ratio
recipes_bivar_2 = recipes_full.copy()

# convert the tags column to a list
recipes_bivar_2['tags'] = recipes_bivar_2['tags'].apply(eval) 

# explode the tags column (one tag per row)
recipes_imputed = recipes_bivar_2.explode('tags')

# isolate the stuff we care about (nutritonal values)
recipes_imputed = recipes_imputed.set_index('recipe_id')[['tags','calories', 'total_fat', 'sugar', 'sodium', 'protein', 'saturated_fat', 'carbohydrates']]
recipes_non_imputed = recipes_imputed.copy()

recipes_imputed = recipes_imputed.dropna()


In [29]:
recipes_non_imputed

tags  calories  total_fat  sugar  sodium  protein  \
recipe_id                                                                    
275022.0   60-minutes-or-less     386.1       34.0    7.0    24.0     41.0   
275022.0         time-to-make     386.1       34.0    7.0    24.0     41.0   
275022.0               course     386.1       34.0    7.0    24.0     41.0   
...                       ...       ...        ...    ...     ...      ...   
537716.0              chicken     407.9       34.0   21.0    49.0     28.0   
537716.0           sandwiches     407.9       34.0   21.0    49.0     28.0   
537716.0                 meat     407.9       34.0   21.0    49.0     28.0   

           saturated_fat  carbohydrates  
recipe_id                                
275022.0            62.0            8.0  
275022.0            62.0            8.0  
275022.0            62.0            8.0  
...                  ...            ...  
537716.0            64.0           12.0  
537716.0            64.0           12.0  
537716.0            64.0           12.0  

[1364760 rows x 8 columns]

In [30]:
recipes_imputed

tags  calories  total_fat  sugar  sodium  protein  \
recipe_id                                                                    
275022.0   60-minutes-or-less     386.1       34.0    7.0    24.0     41.0   
275022.0         time-to-make     386.1       34.0    7.0    24.0     41.0   
275022.0               course     386.1       34.0    7.0    24.0     41.0   
...                       ...       ...        ...    ...     ...      ...   
537716.0              chicken     407.9       34.0   21.0    49.0     28.0   
537716.0           sandwiches     407.9       34.0   21.0    49.0     28.0   
537716.0                 meat     407.9       34.0   21.0    49.0     28.0   

           saturated_fat  carbohydrates  
recipe_id                                
275022.0            62.0            8.0  
275022.0            62.0            8.0  
275022.0            62.0            8.0  
...                  ...            ...  
537716.0            64.0           12.0  
537716.0            64.0           12.0  
537716.0            64.0           12.0  

[1364760 rows x 8 columns]

When examining only nutritional values, the imputed dataset has the same shape as the non-imputed dataset. So in this case, dropping NA values is sufficient (or not doing imputation at all).

## Step 3: Framing a Prediction Problem

Our question is as such: when given a vector of nutritional values, the number of minutes needed to finish the recipe, and the average rating, what would be the predicted number of calories?

This question is a regression problem, since the `calories` column is numerical.


In [31]:
recipes_full = df.copy()
recipes_pred = recipes_full[['calories', 'total_fat', 'sugar', 'sodium', 'protein', 'saturated_fat', 'carbohydrates', 'minutes', 'avg_rating']].dropna()
recipes_pred

calories  total_fat  sugar  sodium  ...  saturated_fat  carbohydrates  \
0         386.1       34.0    7.0    24.0  ...           62.0            8.0   
1         377.1       18.0  208.0    13.0  ...           30.0           20.0   
2         326.6       30.0   12.0    27.0  ...           51.0            5.0   
...         ...        ...    ...     ...  ...            ...            ...   
83776     220.7       15.0   49.0     2.0  ...           30.0            4.0   
83777      52.8        3.0    0.0     4.0  ...            1.0            2.0   
83780     407.9       34.0   21.0    49.0  ...           64.0           12.0   

       minutes  avg_rating  
0           50         3.0  
1           55         3.0  
2           45         3.0  
...        ...         ...  
83776       10         5.0  
83777       45         5.0  
83780       40         5.0  

[81173 rows x 9 columns]

Our response variable will be the predicted `calories`.
We decided to classify this variable because it is easliy interpretable for someone looking to make something with certain caloric needs.
Our metric for success will be mean squared error, as it is the easiest to calculate (although in ridge regression this is not what is minimized). However, this approximation should be enough to estimate the success of the model.

## Step 4: Baseline Model

In [40]:

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import Ridge
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler


baseline_model = make_pipeline(StandardScaler(), Ridge())

# make the train test splits
X_train, X_test, y_train, y_test = train_test_split(recipes_pred[['total_fat', 'sugar', 'sodium', 'protein', 'saturated_fat', 'carbohydrates', 'minutes', 'avg_rating']], 
                                                    recipes_pred['calories'], 
                                                    random_state=26)
# fit the model
baseline_model.fit(X_train, y_train)

# predict the calories
y_pred = baseline_model.predict(X_test)
y_pred



array([177.79, 409.4 , 412.47, ..., 449.72, 289.27, 390.91])

In [41]:
# Evaluate the model using mean squared error
mse = 0
for i in range(len(y_test.values)):
    mse += (y_test.values[i] - y_pred[i])**2

print("Average Mean squared error is", mse/len(y_test.values))


Average Mean squared error is 2324.047870089271


## Step 5: Final Model

We have a few ideas for improvement of the model:

1. Use `sklearn`'s `QuantileTransformer()` on the `minutes` column. This should improve the average mean squared error because the `minutes` column is significantly right skewed, with many outliers.

2. 